In [1]:
# Collect the list of the S&P 500 companies from Wikipedia and save it to a file
import os
import requests
import pandas as pd

# Get the list of S&P 500 companies from Wikipedia
url = 'https://en.wikipedia.org/wiki/List_of_S%26P_500_companies'
response = requests.get(url)
html = response.content
df = pd.read_html(html, header=0)[0]

tickers = df['Symbol'].tolist()
# tickers.append('^GSPC')

In [2]:
# Load the data from yahoo finance
import os
import yfinance as yf

def load_data(symbol):

    direc = 'data/'
    os.makedirs(direc, exist_ok=True)

    file_name = os.path.join(direc, symbol + '.csv')

    if not os.path.exists(file_name):

        ticker = yf.Ticker(symbol)
        df = ticker.history(start='2005-01-01', end='2023-12-31')

        df.to_csv(file_name)

    df = pd.read_csv(file_name, index_col=0)
    df.index = pd.to_datetime(df.index, utc=True).tz_convert('US/Eastern')
    df['date'] = df.index

    if len(df) == 0:
        os.remove(file_name)
        return None

    return df


In [3]:
holder = []
ticker_with_data = []
for symbol in tickers:
    df = load_data(symbol)
    if df is not None:
        holder.append(df)
        ticker_with_data.append(symbol)

tickers = ticker_with_data[:]

print (f'Loaded data for {len(tickers)} companies')


BRK.B: No timezone found, symbol may be delisted
BF.B: No price data found, symbol may be delisted (1d 2005-01-01 -> 2023-12-31)
GEV: Data doesn't exist for startDate = 1104555600, endDate = 1703998800
SOLV: Data doesn't exist for startDate = 1104555600, endDate = 1703998800


Loaded data for 499 companies


In [4]:
# Find cointegrated pairs in the holder
from statsmodels.tsa.stattools import coint
import numpy as np
import itertools


In [5]:

def find_cointegrated_pairs(data):
    n = len(data)

    score_matrix = np.zeros((n, n))
    pvalue_matrix = np.ones((n, n))

    keys = range(n)
    pairs = list(itertools.combinations(keys, 2))

    for i, j in pairs:
        print(f'Finding cointegration for {tickers[i]} and {tickers[j]}')
        try:
            result = coint(data[i]['Close'], data[j]['Close'])
        except:
            print(f'Error in cointegration test for {tickers[i]} and {tickers[j]}')
            continue
        else:
            score = result[0]
            pvalue = result[1]
            score_matrix[i, j] = score
            pvalue_matrix[i, j] = pvalue

    return score_matrix, pvalue_matrix


In [7]:
score_matrix, pvalue_matrix = find_cointegrated_pairs(holder)

Finding cointegration for MMM and AOS
Finding cointegration for MMM and ABT
Finding cointegration for MMM and ABBV
Error in cointegration test for MMM and ABBV
Finding cointegration for MMM and ACN
Finding cointegration for MMM and ADBE
Finding cointegration for MMM and AMD
Finding cointegration for MMM and AES
Finding cointegration for MMM and AFL
Finding cointegration for MMM and A
Finding cointegration for MMM and APD
Finding cointegration for MMM and ABNB
Error in cointegration test for MMM and ABNB
Finding cointegration for MMM and AKAM
Finding cointegration for MMM and ALB
Finding cointegration for MMM and ARE
Finding cointegration for MMM and ALGN
Finding cointegration for MMM and ALLE
Error in cointegration test for MMM and ALLE
Finding cointegration for MMM and LNT
Finding cointegration for MMM and ALL
Finding cointegration for MMM and GOOGL
Finding cointegration for MMM and GOOG
Finding cointegration for MMM and MO
Finding cointegration for MMM and AMZN
Finding cointegration 

In [8]:
# Save the score and pvalue matrix
np.save('score_matrix.npy', score_matrix)
np.save('pvalue_matrix.npy', pvalue_matrix)

In [6]:
# Read the score and pvalue matrix
score_matrix = np.load('score_matrix.npy')
pvalue_matrix = np.load('pvalue_matrix.npy')

In [8]:

pairs = []
for i in range(len(tickers)):
    for j in range(i+1, len(tickers)):
        if pvalue_matrix[i, j] < 0.05:
            pairs.append((tickers[i], tickers[j]))

print (f'Found {len(pairs)} cointegrated pairs')



Found 7995 cointegrated pairs


In [9]:
# Print the top 100 cointegrated pairs with the lowest p-values
pairs.sort(key=lambda x: pvalue_matrix[tickers.index(x[0]), tickers.index(x[1])])
for pair in pairs[:100]:
    print(pair, pvalue_matrix[tickers.index(pair[0]), tickers.index(pair[1])])

('AAPL', 'MPWR') 8.344162226719754e-10
('MPWR', 'ODFL') 2.1921688098373297e-09
('CTAS', 'PGR') 1.584074777053476e-08
('IEX', 'WTW') 4.964450836119244e-08
('MSFT', 'MPWR') 7.561131664837993e-08
('AON', 'ADP') 1.0739720170542662e-07
('DPZ', 'TYL') 2.199622860013937e-07
('AAPL', 'ODFL') 2.602578450245994e-07
('MOH', 'MPWR') 3.1457994708296224e-07
('AXON', 'DHI') 3.2712875621970466e-07
('KLAC', 'SNPS') 3.7120083767609646e-07
('TER', 'WST') 5.156075694192834e-07
('DTE', 'JNJ') 7.241285863540705e-07
('PAYX', 'WM') 7.303717258305525e-07
('DPZ', 'WTW') 7.887833794546992e-07
('JPM', 'SYK') 1.0402646270213549e-06
('TECH', 'TER') 1.0541016718953342e-06
('HD', 'WTW') 1.1478285284550153e-06
('CINF', 'SYY') 1.2106739717195465e-06
('KLAC', 'ODFL') 1.212511869425792e-06
('EXPD', 'INTU') 1.2129537263802449e-06
('MKC', 'WEC') 1.2316872022471847e-06
('CDNS', 'KLAC') 1.2945911273423597e-06
('LH', 'WAT') 1.3612428279732642e-06
('ADP', 'ELV') 1.5489567302867815e-06
('DPZ', 'CRM') 1.601814733691993e-06
('ABT

In [10]:
# Load the data for the top 100 cointegrated pairs
top_pairs = pairs[:100]
top_pairs_data = []
for pair in top_pairs:
    top_pairs_data.append((load_data(pair[0]), load_data(pair[1])))
    print(f'Loaded data for {pair[0]} and {pair[1]}')

Loaded data for AAPL and MPWR
Loaded data for MPWR and ODFL
Loaded data for CTAS and PGR
Loaded data for IEX and WTW
Loaded data for MSFT and MPWR
Loaded data for AON and ADP
Loaded data for DPZ and TYL
Loaded data for AAPL and ODFL
Loaded data for MOH and MPWR
Loaded data for AXON and DHI
Loaded data for KLAC and SNPS
Loaded data for TER and WST
Loaded data for DTE and JNJ
Loaded data for PAYX and WM
Loaded data for DPZ and WTW
Loaded data for JPM and SYK
Loaded data for TECH and TER
Loaded data for HD and WTW
Loaded data for CINF and SYY
Loaded data for KLAC and ODFL
Loaded data for EXPD and INTU
Loaded data for MKC and WEC
Loaded data for CDNS and KLAC
Loaded data for LH and WAT
Loaded data for ADP and ELV
Loaded data for DPZ and CRM
Loaded data for ABT and TDY
Loaded data for ADP and WM
Loaded data for IDXX and TER
Loaded data for LRCX and MPWR
Loaded data for GPN and TFX
Loaded data for ABT and NSC
Loaded data for MMM and IFF
Loaded data for CSCO and CME
Loaded data for SHW and TY

In [11]:
# For each df in the top_pairs_data, devide the close price by the first close price
for i, (df1, df2) in enumerate(top_pairs_data):
    top_pairs_data[i] = (df1['Close'] / df1['Close'].iloc[0], df2['Close'] / df2['Close'].iloc[0])

# Show the top_pairs_data[0]
print(top_pairs_data[0])

(Date
2005-01-03 00:00:00-05:00      1.000000
2005-01-04 00:00:00-05:00      1.010269
2005-01-05 00:00:00-05:00      1.019118
2005-01-06 00:00:00-05:00      1.019908
2005-01-07 00:00:00-05:00      1.094169
                                ...    
2023-12-22 00:00:00-05:00    202.081329
2023-12-26 00:00:00-05:00    201.507220
2023-12-27 00:00:00-05:00    201.611594
2023-12-28 00:00:00-05:00    202.060441
2023-12-29 00:00:00-05:00    200.964442
Name: Close, Length: 4781, dtype: float64, Date
2005-01-03 00:00:00-05:00     1.000000
2005-01-04 00:00:00-05:00     0.975197
2005-01-05 00:00:00-05:00     0.935739
2005-01-06 00:00:00-05:00     0.928974
2005-01-07 00:00:00-05:00     0.930102
                               ...    
2023-12-22 00:00:00-05:00    79.988751
2023-12-26 00:00:00-05:00    82.501179
2023-12-27 00:00:00-05:00    82.439018
2023-12-28 00:00:00-05:00    82.005783
2023-12-29 00:00:00-05:00    81.819005
Name: Close, Length: 4781, dtype: float64)


In [12]:
# For each pair in the top_pairs_data, calculate the spread
spread_data = []
for df1, df2 in top_pairs_data:
    spread_data.append(df1 - df2)
    
# Show the spread_data[0]
print(spread_data[0])

Date
2005-01-03 00:00:00-05:00      0.000000
2005-01-04 00:00:00-05:00      0.035072
2005-01-05 00:00:00-05:00      0.083379
2005-01-06 00:00:00-05:00      0.090934
2005-01-07 00:00:00-05:00      0.164067
                                ...    
2023-12-22 00:00:00-05:00    122.092578
2023-12-26 00:00:00-05:00    119.006040
2023-12-27 00:00:00-05:00    119.172577
2023-12-28 00:00:00-05:00    120.054658
2023-12-29 00:00:00-05:00    119.145437
Name: Close, Length: 4781, dtype: float64


In [13]:
# Calculate the standard deviation of the spread for each pair
std_spread = []
for spread in spread_data:
    std_spread.append(np.std(spread))

# Show the std_spread[0]
print(std_spread[0])

36.3903416617999


In [21]:
# Generate the signals for each pair based on if the absolute value of spread is greater than 2 standard deviation
# If the spread is greater than 2 standard deviation, the signal is 1
# If the spread is less than -2 standard deviation, the signal is -1
# Otherwise, the signal is 0
signals = []
for spread, std in zip(spread_data, std_spread):
    signals.append(np.where(spread > 2 * std, 1, np.where(spread < -2 * std, -1, 0)))

# Show the signals[0]
print(signals[0])


[0 0 0 ... 1 1 1]


In [20]:
# Calculate the daily return for each pair using close price
daily_return = [None] * len(top_pairs_data)
for i, (df1, df2) in enumerate(top_pairs_data):
    daily_return[i] = ((df1/df1.shift(1) - 1) , (df2/df2.shift(1) - 1))

# Show the daily_return[0]
print(daily_return[0])

(Date
2005-01-03 00:00:00-05:00         NaN
2005-01-04 00:00:00-05:00    0.010269
2005-01-05 00:00:00-05:00    0.008759
2005-01-06 00:00:00-05:00    0.000775
2005-01-07 00:00:00-05:00    0.072811
                               ...   
2023-12-22 00:00:00-05:00   -0.005547
2023-12-26 00:00:00-05:00   -0.002841
2023-12-27 00:00:00-05:00    0.000518
2023-12-28 00:00:00-05:00    0.002226
2023-12-29 00:00:00-05:00   -0.005424
Name: Close, Length: 4781, dtype: float64, Date
2005-01-03 00:00:00-05:00         NaN
2005-01-04 00:00:00-05:00   -0.024803
2005-01-05 00:00:00-05:00   -0.040462
2005-01-06 00:00:00-05:00   -0.007229
2005-01-07 00:00:00-05:00    0.001214
                               ...   
2023-12-22 00:00:00-05:00   -0.006578
2023-12-26 00:00:00-05:00    0.031410
2023-12-27 00:00:00-05:00   -0.000753
2023-12-28 00:00:00-05:00   -0.005255
2023-12-29 00:00:00-05:00   -0.002278
Name: Close, Length: 4781, dtype: float64)


In [27]:
# For each pair, calculate the daily return of the strategy
# If the signal is 1, then short the first stock and long the second stock, hold the position until the spread is 0, then calculate the return for this trade
# If the signal is -1, then long the first stock and short the second stock, hold the position until the spread is 0, then calculate the return foer this trade
# If the signal is 0, then do nothing
daily_return_strategy = []
for i, (df1, df2) in enumerate(top_pairs_data):
    signal = signals[i]
    spread = spread_data[i]
    daily_return_strategy.append([0] * len(df1))
    for j in range(1, len(df1)):
        # If the signal is 1 and the previous signal is not 1, then short the first stock and long the second stock
        if signal[j] == 1 and signal[j-1] != 1:
            # Exit the position when the spread is less than or equal to 0
            k = j
            while k < len(df1) and spread[k] > 0:
                k += 1
            if k < len(df1):
                daily_return_strategy[i][j] = (df2[k]/df2[j] - 1) - (df1[k]/df1[j] - 1)
        # If the signal is -1 and the previous signal is not -1, then long the first stock and short the second stock
        elif signal[j] == -1 and signal[j-1] != -1:
            # Exit the position when the spread is greater than or equal to 0
            k = j
            while k < len(df1) and spread[k] < 0:
                k += 1
            if k < len(df1):
                daily_return_strategy[i][j] = (df1[k]/df1[j] - 1) - (df2[k]/df2[j] - 1)

# Show the daily_return_strategy[0]
print(daily_return_strategy[0])

C:\Users\V\AppData\Local\Temp\ipykernel_16616\3335871699.py:15: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  while k < len(df1) and spread[k] > 0:
C:\Users\V\AppData\Local\Temp\ipykernel_16616\3335871699.py:18: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  daily_return_strategy[i][j] = (df2[k]/df2[j] - 1) - (df1[k]/df1[j] - 1)
C:\Users\V\AppData\Local\Temp\ipykernel_16616\3335871699.py:23: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]

[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 

In [28]:
# Calculate the cumulative return for each pair using cumsum
cumulative_return = []
for daily_return_strat in daily_return_strategy:
    cumulative_return.append(np.cumsum(daily_return_strat))

# Show the cumulative_return[0]
print(cumulative_return[0])

[0 0 0 ... 0 0 0]


In [29]:
# Check the non zero cumulative return
for i, cum_return in enumerate(cumulative_return):
    if cum_return[-1] != 0:
        print(f'{top_pairs[i]}: {cum_return[-1]}')


('MPWR', 'ODFL'): 8.657274975706759
('CTAS', 'PGR'): 1.135293225946255
('DPZ', 'TYL'): 10.859920755863499
('AXON', 'DHI'): 1.9177408548282746
('KLAC', 'SNPS'): 9.888987180439472
('JPM', 'SYK'): 5.906123651397874
('CDNS', 'KLAC'): 3.796806655376918
('ADP', 'ELV'): 13.01664043433692
('DPZ', 'CRM'): 6.855129522042045
('ADP', 'WM'): 6.882375533946338
('GPN', 'TFX'): 4.607695194557184
('ABT', 'NSC'): 10.973052045431979
('MMM', 'IFF'): 12.881178543149751
('AIG', 'C'): 2.362466510358973
('CRL', 'ZBRA'): 5.479183780005569
('HUM', 'ROL'): 8.28702619719919
('KO', 'DUK'): 7.675340790144663
('ON', 'STLD'): 13.738560373001402
('AMZN', 'DPZ'): 4.728081096362315
('MKC', 'XEL'): 6.405401556306531
('EIX', 'OMC'): 18.318367137613393
('NEE', 'RMD'): 5.792385120097194
('DUK', 'JNJ'): 20.589929564175662
('CINF', 'PEG'): 10.562221088091666
('SPGI', 'TDY'): 12.497615331689609
('CNC', 'JKHY'): 9.406375381098957
('ES', 'MKC'): 22.779397458776746


In [30]:
# calculate the sharpe ratio for each pair with non zero cumulative return
sharpe_ratio = []
for i, cum_return in enumerate(cumulative_return):
    if cum_return[-1] != 0:
        sharpe_ratio.append(np.mean(daily_return_strategy[i]) / np.std(daily_return_strategy[i]) * np.sqrt(252))

# Show the sharpe_ratio
for i, ratio in enumerate(sharpe_ratio):
    print(f'{top_pairs[i]}: {ratio}')


('AAPL', 'MPWR'): 1.2135911841226716
('MPWR', 'ODFL'): 0.3936914941537538
('CTAS', 'PGR'): 1.4671145452975698
('IEX', 'WTW'): 0.4862061591759105
('MSFT', 'MPWR'): 1.0127656512041063
('AON', 'ADP'): 1.1096330530602938
('DPZ', 'TYL'): 0.8924575280403901
('AAPL', 'ODFL'): 1.519691579409812
('MOH', 'MPWR'): 1.2095112968793247
('AXON', 'DHI'): 1.4045874868210189
('KLAC', 'SNPS'): 0.874490403167645
('TER', 'WST'): 0.919104667825187
('DTE', 'JNJ'): 1.491279140736045
('PAYX', 'WM'): 1.0252128857726421
('DPZ', 'WTW'): 0.9339213333815113
('JPM', 'SYK'): 1.2080968980464608
('TECH', 'TER'): 1.6293635832802171
('HD', 'WTW'): 1.238138616740188
('CINF', 'SYY'): 0.931605895574006
('KLAC', 'ODFL'): 1.1919309235656914
('EXPD', 'INTU'): 1.4512882450194085
('MKC', 'WEC'): 1.024550645534144
('CDNS', 'KLAC'): 1.2702684956727106
('LH', 'WAT'): 0.8438032506813923
('ADP', 'ELV'): 1.351080687404711
('DPZ', 'CRM'): 1.5777825246185813
('ABT', 'TDY'): 1.364831760645795
